## HTS Code Classification Task

The task for the model is to output a 10 digit hts code given a product description.
This is the great usecase for RAG as providing context of hts codes with similar product descriptions can greatly improve the accuracy. The following approach leverages RAG with Databricks vector search and structured JSON outputs to tackle the issues of response inconsistencies and format adherence. 

Details of the approach:
1. Downloaded the HTS catalog data from data.gov: [Harmonized Tariff Schedule of the United States 2024](https://catalog.data.gov/dataset/harmonized-tariff-schedule-of-the-united-states-2024).
2. Processed the data to format it into 10-digit HTS codes with descriptions, resulting in a table of 19,733 HTS codes with descriptions.
3. Set up a vector search endpoint and indexed the table using the databricks-gte-large-en embedding model, with retriever to get relevant rows for a product description
4. Generated 100 random product descriptions. Tested the model on these product descriptions by providing context (RAG) with Structured JSON outputs.


### 1. Download HTS data from .gov and upload file to Databricks volume
https://catalog.data.gov/dataset/harmonized-tariff-schedule-of-the-united-states-2024

In [ ]:
CATALOG = "workspace"
SCHEMA = "default"
FILES_PATH = f"/Volumes/{CATALOG}/{SCHEMA}/files/"

In [ ]:
import pandas as pd
df = pd.read_csv(f"{FILES_PATH}/hts_2025_revision_11_csv.csv")
df.head(10)

HTS Number  Indent  ... Quota Quantity Additional Duties
0           0101       0  ...            NaN               NaN
1            NaN       1  ...            NaN               NaN
2     0101.21.00       2  ...            NaN               NaN
3  0101.21.00.10       3  ...            NaN               NaN
4  0101.21.00.20       3  ...            NaN               NaN
5     0101.29.00       2  ...            NaN               NaN
6  0101.29.00.10       3  ...            NaN               NaN
7  0101.29.00.90       3  ...            NaN               NaN
8  0101.30.00.00       1  ...            NaN               NaN
9        0101.90       1  ...            NaN               NaN

[10 rows x 9 columns]

### 2. Process download file into 10 digit hts_code: description format

In [ ]:
import re

def check_format(s):
    pattern = r'^\d{4}\.\d{2}\.\d{2}\.\d{2}$'
    return bool(re.match(pattern, s))

def code_format(s):
    return s.replace('.', '')

In [ ]:
indentStack = []
descStack = []
data = []

for index, row in df.iterrows():
    while indentStack and row['Indent'] <= indentStack[-1]:
        indentStack.pop()
        descStack.pop()
    indentStack.append(row['Indent'])
    descStack.append(row['Description'])

    if check_format(str(row['HTS Number'])):
        desc = ' '.join(descStack)
        hts_code = code_format(str(row['HTS Number']))
        data.append([hts_code, desc])

display(data)

_1 _2 0101210010 Live horses, asses, mules and hinnies: Horses: Purebred breeding animals Males 0101210020 Live horses, asses, mules and hinnies: Horses: Purebred breeding animals Females 0101290010 Live horses, asses, mules and hinnies: Horses: Other Imported for immediate slaughter 0101290090 Live horses, asses, mules and hinnies: Horses: Other Other 0101300000 Live horses, asses, mules and hinnies: Asses 0101903000 Live horses, asses, mules and hinnies: Other: Imported for immediate slaughter 0101904000 Live horses, asses, mules and hinnies: Other: Other 0102210010 Live bovine animals: Cattle: Purebred breeding animals Dairy: Male 0102210020 Live bovine animals: Cattle: Purebred breeding animals Dairy: Female 0102210030 Live bovine animals: Cattle: Purebred breeding animals Other: Male 0102210050 Live bovine animals: Cattle: Purebred breeding animals Other: Female 0102292011 Live bovine animals: Cattle: Other: Cows imported specially for dairy purposes Weighing less than 90 kg each 0102292012 Live bovine animals: Cattle: Other: Cows imported specially for dairy purposes Weighing 90 kg or more each 0102294024 Live bovine animals: Cattle: Other: Other Weighing less than 90 kg each: Male 0102294028 Live bovine animals: Cattle: Other: Other Weighing less than 90 kg each: Female 0102294034 Live bovine animals: Cattle: Other: Other Weighing 90 kg or more but less than 200 kg each: Male 0102294038 Live bovine animals: Cattle: Other: Other Weighing 90 kg or more but less than 200 kg each: Female 0102294054 Live bovine animals: Cattle: Other: Other Weighing 200 kg or more but less than 320 kg each: Male 0102294058 Live bovine animals: Cattle: Other: Other Weighing 200 kg or more but less than 320 kg each: Female 0102294062 Live bovine animals: Cattle: Other: Other Weighing 320 kg or more each: For immediate slaughter: Steers 0102294064 Live bovine animals: Cattle: Other: Other Weighing 320 kg or more each: For immediate slaughter: Bulls 0102294066 Live bovine animals: Cattle: Other: Other Weighing 320 kg or more each: For immediate slaughter: Cows 0102294068 Live bovine animals: Cattle: Other: Other Weighing 320 kg or more each: For immediate slaughter: Heifers 0102294072 Live bovine animals: Cattle: Other: Other Weighing 320 kg or more each: For breeding: Male 0102294074 Live bovine animals: Cattle: Other: Other Weighing 320 kg or more each: For breeding: Female 0102294082 Live bovine animals: Cattle: Other: Other Weighing 320 kg or more each: Other: Male 0102294084 Live bovine animals: Cattle: Other: Other Weighing 320 kg or more each: Other: Female 0102310010 Live bovine animals: Buffalo: Purebred breeding animals Male 0102310020 Live bovine animals: Buffalo: Purebred breeding animals Female 0102390010 Live bovine animals: Buffalo: Other Bison 0102390024 Live bovine animals: Buffalo: Other Other: Weighing less than 90 kg each: Male 0102390028 Live bovine animals: Buffalo: Other Other: Weighing less than 90 kg each: Female 0102390034 Live bovine animals: Buffalo: Other Other: Weighing 90 kg or more but less than 200 kg each: Male 0102390038 Live bovine animals: Buffalo: Other Other: Weighing 90 kg or more but less than 200 kg each: Female 0102390054 Live bovine animals: Buffalo: Other Other: Weighing 200 kg or more but less than 320 kg each: Male 0102390058 Live bovine animals: Buffalo: Other Other: Weighing 200 kg or more but less than 320 kg each: Female 0102390061 Live bovine animals: Buffalo: Other Other: Weighing 320 kg or more each: For immediate slaughter 0102390072 Live bovine animals: Buffalo: Other Other: Weighing 320 kg or more each: For breeding: Male 0102390074 Live bovine animals: Buffalo: Other Other: Weighing 320 kg or more each: For breeding: Female 0102390082 Live bovine animals: Buffalo: Other Other: Weighing 320 kg or more each: Other: Male 0102390084 Live bovine animals: Buffalo: Other Other: Weighing 320 kg or more each: Other: Female 0102900000 Live bovine animals: Other 0103100000 Live swine: Purebred breed

In [ ]:
df = pd.DataFrame(data, columns=['hts_code', 'description'])
df.head()

hts_code                                        description
0  0101210010  Live horses, asses, mules and hinnies: Horses:...
1  0101210020  Live horses, asses, mules and hinnies: Horses:...
2  0101290010  Live horses, asses, mules and hinnies: Horses:...
3  0101290090  Live horses, asses, mules and hinnies: Horses:...
4  0101300000       Live horses, asses, mules and hinnies: Asses

In [ ]:
df.to_json(f"{FILES_PATH}/hts_2025_revision_11_clean.json", orient='records')
df.to_csv(f"{FILES_PATH}/hts_2025_revision_11_clean.csv")

In [ ]:
import pandas as pd
dtype = {
    'hts_code': str,
    'description': str
}
df = pd.read_json(f"{FILES_PATH}/hts_2025_revision_11_clean.json", dtype=dtype)
df.head()

hts_code                                        description
0  0101210010  Live horses, asses, mules and hinnies: Horses:...
1  0101210020  Live horses, asses, mules and hinnies: Horses:...
2  0101290010  Live horses, asses, mules and hinnies: Horses:...
3  0101290090  Live horses, asses, mules and hinnies: Horses:...
4  0101300000       Live horses, asses, mules and hinnies: Asses

In [ ]:
df.shape

(19733, 2)

### 3. Store the cleaned data into table (hts_code, description)
Creating table hts_description

In [ ]:
%sql
CREATE TABLE IF NOT EXISTS workspace.default.hts_description (hts_code STRING, description STRING, id BIGINT GENERATED BY DEFAULT AS IDENTITY) tblproperties (delta.autoOptimize.optimizeWrite = true, delta.enableChangeDataFeed = true);

In [ ]:
from pyspark.sql import functions as F

# Convert pandas DataFrame to Spark DataFrame
spark_df = spark.createDataFrame(df)

# Add an incremental id column
spark_df_with_id = spark_df.withColumn("id", F.monotonically_increasing_id())

# Select and reorder columns to match the target table schema
final_df = spark_df_with_id.select("hts_code", "description", "id")

# Write to the target table
final_df.write.insertInto(f"{CATALOG}.{SCHEMA}.hts_description", overwrite=False)

In [ ]:
%sql
select count(*) from workspace.default.hts_description

count(*) 19733

### 4. Set up Databricks vector search
1. Create a vector search endpoint from UI (Compute -> Vector Search -> Create)
2. Create vector search index on the table: Once the endpoint is provisioned, go to the hts_description table in the catalog created in previous steps, in create drop down select Create vector Index

### 5. Get vector store retriever

In [ ]:
%pip install databricks-vectorsearch
dbutils.library.restartPython()


Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [ ]:
import os
from databricks.vector_search.client import VectorSearchClient

vsc = VectorSearchClient()

index = vsc.get_index(endpoint_name="hts_vector_search", index_name="workspace.default.hts_idx")

index.similarity_search(num_results=3, columns=["hts_code","description"], query_text="women's under pants")

[NOTICE] Using a notebook authentication token. Recommended for development only. For improved performance, please use Service Principal based authentication. To disable this message, pass disable_notice=True.
[NOTICE] Using a notebook authentication token. Recommended for development only. For improved performance, please use Service Principal based authentication. To disable this message, pass disable_notice=True.


{'manifest': {'column_count': 3,
  'columns': [{'name': 'hts_code'},
   {'name': 'description'},
   {'name': 'score'}]},
 'result': {'row_count': 3,
  'data_array': [['6108910005',
    "Women's or girls' slips, petticoats, briefs, panties, night dresses, pajamas, negligees, bathrobes, dressing gowns and similar articles, knitted or crocheted: Other: Of cotton Underwear: Underpants (352)",
    0.0031505523],
   ['6108920005',
    "Women's or girls' slips, petticoats, briefs, panties, night dresses, pajamas, negligees, bathrobes, dressing gowns and similar articles, knitted or crocheted: Other: Of man-made fibers Underwear: Underpants (652)",
    0.0031227614],
   ['6208913010',
    "Women's or girls' singlets and other undershirts, slips, petticoats, briefs, panties, nightdresses,   pajamas, negligees, bathrobes, dressing gowns and similar articles: Other: Of cotton: Other Women's (352)",
    0.0028401248]]},
 'debug_info': {'response_time': 112.0,
  'ann_time': 17.0,
  'embedding_gen_t

In [ ]:
%pip install -qU databricks-langchain langchain langchain_community
dbutils.library.restartPython()

Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [ ]:
from databricks.vector_search.client import VectorSearchClient
from databricks_langchain import DatabricksVectorSearch

def get_retriever(persist_dir: str = None):
    #Get the vector search index
    # vsc = VectorSearchClient(workspace_url=host, personal_access_token=os.environ[\"DATABRICKS_TOKEN\"])
    vsc = VectorSearchClient()
    vs_index = vsc.get_index(
        endpoint_name="hts_vector_search",
        index_name="workspace.default.hts_idx")

    # Create the retriever
    vectorstore = DatabricksVectorSearch(
        index_name="workspace.default.hts_idx",
        endpoint="hts_vector_search",
        # text_column="description",
        columns=["hts_code","description"],
        # num_results=5,
        )
    return vectorstore.as_retriever(search_kwargs={"k": 10})

In [ ]:
retriever=get_retriever()
retriever.invoke("Girls beads bracelet handmade")

[NOTICE] Using a notebook authentication token. Recommended for development only. For improved performance, please use Service Principal based authentication. To disable this message, pass disable_notice=True.
[NOTICE] Using a notebook authentication token. Recommended for development only. For improved performance, please use Service Principal based authentication. To disable this message, pass disable_notice=True.


[Document(metadata={'hts_code': '6106202030', 'id': 10289.0}, page_content="Women's or girls' blouses and shirts, knitted or crocheted: Of man-made fibers: Other Girls': Other (639)"),
 Document(metadata={'hts_code': '6106100030', 'id': 10284.0}, page_content="Women's or girls' blouses and shirts, knitted or crocheted: Of cotton Girls': Other (339)"),
 Document(metadata={'hts_code': '7117901000', 'id': 13367.0}, page_content='Imitation jewelry: Other: Necklaces, valued not over 30 cents per dozen, composed wholly of plastic shapes mounted on fiber string'),
 Document(metadata={'hts_code': '7018101000', 'id': 13146.0}, page_content='Glass beads, imitation pearls, imitation precious or semiprecious stones and similar glass smallwares and articles thereof other than imitation jewelry; glass eyes other than prosthetic articles; statuettes and other ornaments of lamp-worked glass, other than imitation jewelry; glass microspheres not exceeding 1 mm in diameter: Glass beads, imitation pearls,

In [ ]:
# Append meta data (hts_code) to retrieved docs page content for passing in context
def format_context(documents):
    context = ""
    for doc in documents:
        context += f"HTS Code: {doc.metadata['hts_code']}, Description: {doc.page_content}\n"
    return context

In [ ]:
def get_context(product: str):
    retriever=get_retriever()
    docs = retriever.invoke(product)
    context = format_context(docs)
    return context


### 6. Generate synthetic test dataset: list of product descriptions

In [ ]:
%pip install openai

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 0.0/680.4 kB ? eta -:--:--
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 680.4/680.4 kB 7.2 MB/s eta 0:00:00
Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [ ]:
from openai import OpenAI
import os
# How to get your Databricks token: https://docs.databricks.com/en/dev-tools/auth/pat.html
# DATABRICKS_TOKEN = os.environ.get('DATABRICKS_TOKEN')
# Alternatively in a Databricks notebook you can use this:
# DATABRICKS_TOKEN = dbutils.notebook.entry_point.getDbutils().notebook().getContext().apiToken().get()

client = OpenAI(
    api_key="<YOUR_DATABRICKS_TOKEN>",
    base_url="https://<YOUR_BASE_URL>.cloud.databricks.com/serving-endpoints"
)

In [ ]:
response_schema = {
    "type": "array",
    "items": {
        "type": "object",
        "properties": {
            "prompt": {"type": "string"},
            "expected_response": {"type": "string"},
        },
        "required": ["prompt", "expected_response"],
    },
}
response_format = {
    "type": "json_schema",
    "json_schema": {
    "name": "hts_classification",
    "schema": response_schema,
    "strict": True
    }
}

response = client.chat.completions.create(
    model="databricks-llama-4-maverick",
    messages=[
        {
            "role": "system",
            "content": "You are an AI assistant for Harmonic tariff system code classification. You help generate a dataset with different product descriptions"
        },
        {
            "role": "user",
            "content": f"""Generate 100 different product descriptions and their best matching 10 digit hts code in JSON.
            An example product description is: `Women's knit warm-wear underpants 67% acrylic 29% rayon (viscose) 4% spandex with full elastic waist`, expected_response: 6108910005 """
        }
    ],
    response_format=response_format

)

print(response.choices[0].message.content)

[
    {
        "prompt": "Men's cotton trousers with 100% cotton fabric",
        "expected_response": "6203422010"
    },
    {
        "prompt": "Women's knit warm-wear underpants 67% acrylic 29% rayon (viscose) 4% spandex with full elastic waist",
        "expected_response": "6108910005"
    },
    {
        "prompt": "Baby boys' cotton rompers with snap fasteners, 100% cotton",
        "expected_response": "6111202000"
    },
    {
        "prompt": "Infant girls' cotton dresses with embroidery, 100% cotton",
        "expected_response": "6114302010"
    },
    {
        "prompt": "Men's cotton dress shirts with button-down collar, 100% cotton",
        "expected_response": "6105100010"
    },
    {
        "prompt": "Women's woven cotton blouses with floral print, 100% cotton",
        "expected_response": "6206303010"
    },
    {
        "prompt": "Girls' knit cotton leggings with elastic waist, 95% cotton 5% elastane",
        "expected_response": "6115122000"
    },
    {
  

#### Note: The expected response for the generated test data might not accurately reflect the product description, so it can be disregarded.

In [ ]:
import pandas as pd
import json
data = json.loads(response.choices[0].message.content)
df = pd.DataFrame(data)
df.head()

prompt expected_response
0  Men's cotton woven shirts with button-down col...        6205202010
1  Baby girls' cotton dresses with floral print a...        6209320040
2  Women's knit warm-wear underpants 67% acrylic ...        6108910005
3  Leather handbags with chain strap and gold-ton...        4202210030
4  Sports shoes with synthetic upper and rubber sole        6402999040

In [ ]:
df.to_json(f"{FILES_PATH}/hts_test_data_v1.json", orient='records')

### 7. Test the model performance
1. Use structured outputs to avoid format issues
2. Pass in context from vector search

In [ ]:

response_schema = {
    "type": "object",
    "properties": {
        "hts_code": {"type": "string"},
        "reason": {"type": "string"},
    },
    "required": ["reason"],
}
response_format = {
      "type": "json_schema",
      "json_schema": {
        "name": "hts_classification",
        "schema": response_schema,
        "strict": True
      }
    }

def get_response(product: str, context: str):
    response = client.chat.completions.create(
        model="databricks-llama-4-maverick",
        messages=[
            {
                "role": "system",
                "content": "You are an AI assistant for Harmonic tariff system code classification. You are given the context to answer with a hts code for user's question. Your response should only be based on the given context and do not use anything else."
            },
            {
                "role": "user",
                "content": f"""Given the context with hts codes and their product descriptions, output the best matching 10 digit hts code for the given product description in JSON with reason. \n
                {context} \n
                Product description: {product}\n
                Best matching 10 digit hts code: \n"""
            }
        ],
        response_format=response_format
    )
    return response.choices[0].message.content

In [ ]:

df[['context', 'response', 'generated_hts_code', 'generated_reason']] = df['prompt'].apply(lambda x: pd.Series([context := get_context(x), response := json.loads(get_response(x, context)), response['hts_code'], response['reason']]))

[NOTICE] Using a notebook authentication token. Recommended for development only. For improved performance, please use Service Principal based authentication. To disable this message, pass disable_notice=True.
[NOTICE] Using a notebook authentication token. Recommended for development only. For improved performance, please use Service Principal based authentication. To disable this message, pass disable_notice=True.
[NOTICE] Using a notebook authentication token. Recommended for development only. For improved performance, please use Service Principal based authentication. To disable this message, pass disable_notice=True.
[NOTICE] Using a notebook authentication token. Recommended for development only. For improved performance, please use Service Principal based authentication. To disable this message, pass disable_notice=True.
[NOTICE] Using a notebook authentication token. Recommended for development only. For improved performance, please use Service Principal based authentication. T

In [ ]:
df.head()

prompt  ...                                   generated_reason
0  Men's cotton woven shirts with button-down col...  ...  The product is described as 'Men's cotton wove...
1  Baby girls' cotton dresses with floral print a...  ...  The product is a baby girl's cotton dress, whi...
2  Women's knit warm-wear underpants 67% acrylic ...  ...  The product is women's knit underpants made of...
3  Leather handbags with chain strap and gold-ton...  ...  The product is described as leather handbags, ...
4  Sports shoes with synthetic upper and rubber sole  ...  The product description 'Sports shoes with syn...

[5 rows x 6 columns]

In [ ]:
df.to_json(f"{FILES_PATH}/hts_test_data_v1_results.json", orient='records')

In [ ]:
df.to_csv(f"{FILES_PATH}/hts_test_data_v1_results.csv")